In [1]:
using Plots
plotlyjs()

INFO: Recompiling stale cache file /Users/derekfulton/.julia/lib/v0.6/PlotUtils.ji for module PlotUtils.
INFO: Recompiling stale cache file /Users/derekfulton/.julia/lib/v0.6/PlotThemes.ji for module PlotThemes.


Plots.PlotlyJSBackend()

# Clione.m

In [39]:
function Clione()
    Total_Neurons = 8;  #Solve for this number of interacting Neurons
    DT = 0.02;  #Time increment as fraction of time constant
    Final_Time = 50;   #Final time value for calculation
    Last = Int64(Final_Time/DT + 1);  #Last time step
    Time = DT*(0:Last-1);  #Time vector
    Tau = 0.8;  #Neural time constants in msec
    TauR = 1.9
    WTS = [1 2 2 1];  #Runge-Kutta Coefficient weights
    
    # Predefine X, K and WTS for speed
    X = Array{Float64}(Total_Neurons, Last)
    K = Array{Float64}(Total_Neurons, 4)
    Weights = Array{Float64}(Total_Neurons, 4)
    
    for NU = 1:Total_Neurons;  #Initialize
        X[NU, :] = zeros(1, Last);  #Vector to store response of Neuron #1
        K[NU, :] = zeros(1, 4);  #Runge-Kutta terms	
        Weights[NU, :] = WTS;  #Make into matrix for efficiency in main loop
    end
    
    X[1, 1] = -0.70;  #Initial conditions here if different from zero
    X[2, 1] = 0.088;  #Initial conditions here if different from zero
    X[3, 1] = -0.70;  #Initial conditions here if different from zero
    X[4, 1] = 0.088;  #Initial conditions here if different from zero
    Wt2 = [0 .5 .5 1];  #Second set of RK weights
    rkIndex = [1 1 2 3]
    Stim1 = 1#input("Stimulating current strength, neuron 1 (red) (0-2): ")
    Stim2 = 0
    ES = 100#input("Inhibitory synaptic conductance factor (0-320): ")
    SynThresh = -0.2;  #Threshold for IPSP conductance change
    #**********
    TauSyn = 1.0;  #IPSP time constant
    #**********
    ST = 10.6
    for T = 2:Last
      for rk = 1:4  #Fourth Order Runge-Kutta
        XH = X[:, T-1] + K[:, rkIndex[rk]]*Wt2[rk]
        Tme =Time[T-1] + Wt2[rk]*DT;  #Time upgrade

        K[1, rk] = DT/Tau*(-(17.81 + 47.71*XH[1] + 32.63*XH[1]^2)*(XH[1] - 0.55) - 26*XH[2]*(XH[1] + 0.92) + Stim1*(Tme > 2)*(Tme <= 3) - ES*XH[7]*(XH[1] + 0.92));  
        K[2, rk] = DT/TauR*(-XH[2] + 1.35*XH[1] + 1.03)
        K[5, rk] = DT/TauSyn*(-XH[5] + (XH[3] > SynThresh))
        K[7, rk] = DT/TauSyn*(-XH[7] + XH[5])

        K[3, rk] = DT/Tau*(-(17.81 + 47.71*XH[3] + 32.63*XH[3]^2)*(XH[3] - 0.55) - 26*XH[4]*(XH[3] + 0.92)+ Stim2*(Tme > 2)*(Tme <= 3) - ES*XH[8]*(XH[3] + 0.92));  
        K[4, rk] = DT/TauR*(-XH[4] + 1.35*XH[3] + 1.03)
        K[6, rk] = DT/TauSyn*(-XH[6] + (XH[1] > SynThresh))
        K[8, rk] = DT/TauSyn*(-XH[8] + XH[6])

     end
        X[:, T] = X[:, T-1] + sum((Weights.*K)', 1)'/6
    end
    
    ### PlotlyJS ###
    trace1 = PlotlyJS.scatter(;x=Time, y=100*X[1, :], mode="lines", line_color="red")
    trace2 = PlotlyJS.scatter(;x=Time, y=100*X[3, :], mode="lines", line_color="blue")
    layout = PlotlyJS.Layout(title="Solutions", xlabel="Time (ms)", ylabel="Voltage (mV)")
    p1 = PlotlyJS.plot([trace1, trace2], layout)
    ### PlotlyJS ###
#     figure(1), ZA = plot(Time, 100*X[1, :], "r', Time, 100*X[3, :] - 150, 'b-'); set(ZA, 'LineWidth", 2)
#     ylabel("V (mV'); xlabel('Time (ms)")
    VV = -0.9:0.01:1.5
    DVdt = -0.5*((1.37 + 3.67*VV + 2.51*VV.^2).*(VV - 0.55) - Stim1/13)./(VV + 0.92)
    DRdt = 1.35*VV + 1.03
    
    ### PlotlyJS ###
    trace1 = PlotlyJS.scatter(;x=VV, y=DVdt, mode="lines", line_color="black")
    trace2 = PlotlyJS.scatter(;x=VV, y=DRdt, mode="lines", line_color="blue")
    trace3 = PlotlyJS.scatter(;x=X[1, :], y=X[2, :], mode="lines", line_color="red")
    layout = PlotlyJS.Layout()
    ### PlotlyJS ###
    
#     figure(2), ZB = plot(VV, DVdt, "k-', VV, DRdt, 'b-', X[1, :], X[2, :], 'r-"); axis([-1, 0.6, 0, 1])
#     set(ZB, "LineWidth", 2); axis square
    #Next lines calculate spike rate
    Spikes = (X[1, 1:Last - 1] .< -0.2).*(X[1, 2:Last] .>= -0.2)
    SpkTime = zeros(1, sum(Spikes))
    Nspk = 1;  #Number of spike
    
    for T = 1:length(Spikes);  #Calculate spike rate for all interspike intervals
        if Spikes[T] == 1; SpkTime[Nspk] = T*DT; Nspk = Nspk + 1; end
    end
    
    Final = length(SpkTime)
    Rates = 1000./(SpkTime[2:Final] - SpkTime[1:Final - 1])
    Leng = length(Rates)
    start = Int64(round(Leng/2))
    Red_Rate = mean(Rates[start:Leng])
    #Next lines calculate blue spike rate
    Spikes = (X[3, 1:Last - 1] .< -0.2).*(X[3, 2:Last] .>= -0.2)
    SpkTime = zeros(1, sum(Spikes))
    Nspk = 1;  #Number of spike
    for T = 1:length(Spikes);  #Calculate spike rate for all interspike intervals
        if Spikes[T] == 1; SpkTime[Nspk] = T*DT; Nspk = Nspk + 1; end
    end
    Final = length(SpkTime)
    BRates = 1000./(SpkTime[2:Final] - SpkTime[1:Final - 1])
    Leng = length(BRates)
    start = Int64(round(Leng/2))
    Blue_Rate = mean(BRates[start:Leng])
    p1
end

Clione (generic function with 1 method)

In [40]:
Clione()

# ESPinteractions.m

In [41]:
function ESPinteractions()
    Total_Neurons = 8;  #Solve for this number of interacting Neurons
    DT = 0.02;  #Time increment as fraction of time constant
    Final_Time = 300;   #Final time value for calculation
    Last = Int64(Final_Time/DT + 1);  #Last time step
    Time = DT*(0:Last-1);  #Time vector
    Tau = 0.97;  #Neural time constants in msec
    TauR = 5.6
    WTS = [1 2 2 1];  #Runge-Kutta Coefficient weights

    # Predefine X, K and WTS for speed
    X = Array{Float64}(Total_Neurons, Last)
    K = Array{Float64}(Total_Neurons, 4)
    Weights = Array{Float64}(Total_Neurons, 4)
    
    for NU = 1:Total_Neurons;  #Initialize
        X[NU, :] = zeros(1, Last);  #Vector to store response of Neuron #1
        K[NU, :] = zeros(1, 4);  #Runge-Kutta terms	
        Weights[NU, :] = WTS;  #Make into matrix for efficiency in main loop
    end


    for NU = 1:Total_Neurons;  #Initialize
        X[NU, :] = zeros(1, Last);  #Vector to store response of Neuron #1
        K[NU, :] = zeros(1, 4);  #Runge-Kutta terms	
        Weights[NU, :] = WTS;  #Make into matrix for efficiency in main loop
    end
    X[1, 1] = -0.754;  #Initial conditions here if different from zero
    X[2, 1] = 0.279;  #Initial conditions here if different from zero
    X[3, 1] = -0.754;  #Initial conditions here if different from zero
    X[4, 1] = 0.279;  #Initial conditions here if different from zero
    Wt2 = [0 .5 .5 1];  #Second set of RK weights
    rkIndex = [1 1 2 3]
    Stim1 = 2#input("Stimulating current strength, neuron 1 (red) (0-2): ")
    Stim2 = 1#input("Stimulating current strength, neuron 2 (blue) (0-2): ")
    ES = 5#input("Excitatory synaptic conductance factor (0-10): ")

    #**********
    TauSyn = 2;  #IPSP time constant
    #**********

    SynThresh = -0.2*1.5;  #Threshold for IPSP conductance change
    ST = 10.6
    for T = 2:Last
      for rk = 1:4  #Fourth Order Runge-Kutta
        XH = X[:, T-1] + K[:, rkIndex[rk]]*Wt2[rk]
        Tme =Time[T-1] + Wt2[rk]*DT;  #Time upgrade

        K[1, rk] = DT/Tau*(-(17.81 + 47.58*XH[1] + 33.8*XH[1]^2)*(XH[1] - 0.48) - 26*XH[2]*(XH[1] + 0.95) + Stim1 - ES*XH[7]*(XH[1]));  
        K[2, rk] = DT/TauR*(-XH[2] + 1.29*XH[1] + 0.79 + 3.3*(XH[1] + 0.38)^2)
        K[5, rk] = DT/TauSyn*(-XH[5] + (XH[3] > SynThresh))
        K[7, rk] = DT/TauSyn*(-XH[7] + XH[5])

        K[3, rk] = DT/Tau*(-(17.81 + 47.58*XH[3] + 33.8*XH[3]^2)*(XH[3] - 0.48) - 26*XH[4]*(XH[3] + 0.95)+ Stim2 - ES*XH[8]*(XH[3]));  
        K[4, rk] = DT/TauR*(-XH[4]+ 1.29*XH[3] + 0.79 + 3.3*(XH[3] + 0.38)^2)
        K[6, rk] = DT/TauSyn*(-XH[6] + (XH[1] > SynThresh))
        K[8, rk] = DT/TauSyn*(-XH[8] + XH[6])

     end
        X[:, T] = X[:, T-1] + sum((Weights.*K)', 1)'/6
    end

    ### PlotlyJS ###
    trace1 = PlotlyJS.scatter(;x=Time, y=100*X[1, :], mode="lines", line_color="red")
    trace2 = PlotlyJS.scatter(;x=Time, y=100*X[3, :], mode="lines", line_color="blue")
    layout = PlotlyJS.Layout(title="Solution", xlabel="Time (ms)", ylabel="Voltage (mV)")
    p1 = PlotlyJS.plot([trace1, trace2], layout)
    ### PlotlyJS ###
#     figure(1), ZA = plot(Time, 100*X[1, :], "r-', Time, 100*X[3, :], 'b-'); set(ZA, 'LineWidth", 2)
    
    #VV = -0.9:0.01:1.5
    #DVdt = -0.5*((1.37 + 3.67*VV + 2.51*VV.^2).*(VV - 0.55) - Stim1/13)./(VV + 0.92)
    #DRdt = 1.35*VV + 1.03
    #Next lines calculate spike rate
    Spikes = (X[1, 1:Last - 1] .< -0.2).*(X[1, 2:Last] .>= -0.2)
    SpkTime = zeros(1, sum(Spikes))
    Nspk = 1;  #Number of spike
    for T = 1:length(Spikes);  #Calculate spike rate for all interspike intervals
        if Spikes[T] == 1; SpkTime[Nspk] = T*DT; Nspk = Nspk + 1; end
    end
    Final = length(SpkTime)
    Rates = 1000./(SpkTime[2:Final] - SpkTime[1:Final - 1])
    Leng = length(Rates)
    Red_Rate = mean(Rates[Int64(round(Leng/2)):Leng])
    #Next lines calculate blue spike rate
    Spikes = (X[3, 1:Last - 1] .< -0.2).*(X[3, 2:Last] .>= -0.2)
    SpkTime = zeros(1, sum(Spikes))
    Nspk = 1;  #Number of spike
    for T = 1:length(Spikes);  #Calculate spike rate for all interspike intervals
        if Spikes[T] == 1; SpkTime[Nspk] = T*DT; Nspk = Nspk + 1; end
    end
    Final = length(SpkTime)
    BRates = 1000./(SpkTime[2:Final] - SpkTime[1:Final - 1])
    Leng = length(BRates)
    Blue_Rate = mean(BRates[Int64(round(Leng/2)):Leng])
    
    p1
end

ESPinteractions (generic function with 1 method)

In [38]:
ESPinteractions()

# ISPinteractions.m

In [44]:
function ISPinteractions()
    Total_Neurons = 8;  #Solve for this number of interacting Neurons
    DT = 0.02;  #Time increment as fraction of time constant
    Final_Time = 3*100;   #Final time value for calculation
    Last = Int64(Final_Time/DT + 1);  #Last time step
    Time = DT*(0:Last-1);  #Time vector
    Tau = 0.97;  #Neural time constants in msec
    TauR = 5.6
    WTS = [1 2 2 1];  #Runge-Kutta Coefficient weights

    # Predefine X, K and WTS for speed
    X = Array{Float64}(Total_Neurons, Last)
    K = Array{Float64}(Total_Neurons, 4)
    Weights = Array{Float64}(Total_Neurons, 4)

    for NU = 1:Total_Neurons;  #Initialize
        X[NU, :] = zeros(1, Last);  #Vector to store response of Neuron #1
        K[NU, :] = zeros(1, 4);  #Runge-Kutta terms	
        Weights[NU, :] = WTS;  #Make into matrix for efficiency in main loop
    end
    X[1, 1] = -0.754;  #Initial conditions here if different from zero
    X[2, 1] = 0.279;  #Initial conditions here if different from zero
    X[3, 1] = -0.754;  #Initial conditions here if different from zero
    X[4, 1] = 0.279;  #Initial conditions here if different from zero
    Wt2 = [0 .5 .5 1];  #Second set of RK weights
    rkIndex = [1 1 2 3]
    Stim1 = 1#input("Stimulating current strength, neuron 1 (red) (0-2): ")
    Stim2 = 2#input("Stimulating current strength, neuron 2 (blue) (0-2): ")
    ES = 4#input("Inhibitory synaptic conductance factor (0-6): ")

    #**********
    TauSyn = 1.27;  #IPSP time constant
    #**********

    SynThresh = -0.2;  #Threshold for IPSP conductance change

    ST = 10.6
    for T = 2:Last
      for rk = 1:4  #Fourth Order Runge-Kutta
        XH = X[:, T-1] + K[:, rkIndex[rk]]*Wt2[rk]
        Tme =Time[T-1] + Wt2[rk]*DT;  #Time upgrade

        K[1, rk] = DT/Tau*(-(17.81 + 47.58*XH[1] + 33.8*XH[1]^2)*(XH[1] - 0.48) - 26*XH[2]*(XH[1] + 0.95) + Stim1 - ES*XH[7]*(XH[1] + 0.92));  
        K[2, rk] = DT/TauR*(-XH[2] + 1.29*XH[1] + 0.79 + 3.3*(XH[1] + 0.38)^2)
        K[5, rk] = DT/TauSyn*(-XH[5] + (XH[3] > SynThresh))
        K[7, rk] = DT/TauSyn*(-XH[7] + XH[5])

        K[3, rk] = DT/Tau*(-(17.81 + 47.58*XH[3] + 33.8*XH[3]^2)*(XH[3] - 0.48) - 26*XH[4]*(XH[3] + 0.95)+ Stim2 - ES*XH[8]*(XH[3] + 0.92));  
        K[4, rk] = DT/TauR*(-XH[4]+ 1.29*XH[3] + 0.79 + 3.3*(XH[3] + 0.38)^2)
        K[6, rk] = DT/TauSyn*(-XH[6] + (XH[1] > SynThresh))
        K[8, rk] = DT/TauSyn*(-XH[8] + XH[6])

     end
        X[:, T] = X[:, T-1] + sum((Weights.*K)', 1)'/6
    end

    ### PlotlyJS ###
    trace1 = PlotlyJS.scatter(;x=Time, y=100*X[1, :], mode="lines", line_color="red")
    trace2 = PlotlyJS.scatter(;x=Time, y=100*X[3, :], mode="lines", line_color="blue")
    layout = PlotlyJS.Layout(title="Solutions", xlabel="Time (ms)", ylabel="Voltage (mV)")
    p1 = PlotlyJS.plot([trace1, trace2], layout)
    ### PlotlyJS ###

#     figure(1), ZA = plot(Time, 100*X[1, :], "r-', Time, 100*X[3, :], 'b-'); set(ZA, 'LineWidth", 2)
#     xlabel("Time (ms)'); ylabel ('V(t)")
    VV = -0.9:0.01:1.5
    DVdt = -0.5*((1.37 + 3.67*VV + 2.51*VV.^2).*(VV - 0.55) - Stim1/13)./(VV + 0.92)
    DRdt = 1.35*VV + 1.03
    #Next lines calculate spike rate
    Spikes = (X[1, 1:Last - 1] .< -0.2).*(X[1, 2:Last] .>= -0.2)
    SpkTime = zeros(1, sum(Spikes))
    Nspk = 1;  #Number of spike
    for T = 1:length(Spikes);  #Calculate spike rate for all interspike intervals
        if Spikes[T] == 1; SpkTime[Nspk] = T*DT; Nspk = Nspk + 1; end
    end
    Final = length(SpkTime)
    Rates = 1000./(SpkTime[2:Final] - SpkTime[1:Final - 1])
    Leng = length(Rates)
    Red_Rate = mean(Rates[Int64(round(Leng/2)):Leng])
    #Next lines calculate blue spike rate
    Spikes = (X[3, 1:Last - 1] .< -0.2).*(X[3, 2:Last] .>= -0.2)
    SpkTime = zeros(1, sum(Spikes))
    Nspk = 1;  #Number of spike
    for T = 1:length(Spikes);  #Calculate spike rate for all interspike intervals
        if Spikes[T] == 1; SpkTime[Nspk] = T*DT; Nspk = Nspk + 1; end
    end
    Final = length(SpkTime)
    BRates = 1000./(SpkTime[2:Final] - SpkTime[1:Final - 1])
    Leng = length(BRates)
    Blue_Rate = mean(BRates[Int64(round(Leng/2)):Leng])
    
    p1
end

ISPinteractions (generic function with 1 method)

In [45]:
ISPinteractions()

# LGN2cell.m

In [53]:
function LGN2cell()
    Total_Equations = 12;  #Solve for this number of interacting Neurons
    DT = 0.1;  #Time increment
    Final_Time = 1000;   #Final time value for calculation
    Last = Int64(Final_Time/DT + 1);  #Last time step
    Time = DT*(0:Last-1);  #Time vector
    Tau = 0.97;  #Neural time constants in msec
    TauR = 5.6
    TauC = 30;  #Tau for Ca++ entry
    TauH = 100;  #Tau for Iahp potential
    WTS = [1 2 2 1];  #Runge-Kutta Coefficient weights

    # Predefine X, K and WTS for speed
    X = Array{Float64}(Total_Equations, Last)
    K = Array{Float64}(Total_Equations, 4)
    Weights = Array{Float64}(Total_Equations, 4)

    for NU = 1:Total_Equations;  #Initialize
    X[NU, :] = zeros(1, Last);  #Vector to store response of Neuron #1
    K[NU, :] = zeros(1, 4);  #Runge-Kutta terms	
    Weights[NU, :] = WTS;  #Make into matrix for efficiency in main loop
    end

    X[1, 1] = -0.736;  #Initial conditions here if different from zero
    X[2, 1] = 0.258;  #Initial conditions here if different from zero
    X[3, 1] = 0.095;  #Initial conditions here if different from zero
    X[4, 1] = 0.323;  #Initial conditions here if different from zero
    X[5, 1] = -0.736;  #Initial conditions here if different from zero
    X[6, 1] = 0.258;  #Initial conditions here if different from zero
    X[7, 1] = 0.095;  #Initial conditions here if different from zero
    X[8, 1] = 0.323;  #Initial conditions here if different from zero
    Wt2 = [0 .5 .5 1];  #Second set of RK weights
    rkIndex = [1 1 2 3]
    SynThresh = -0.2;  #Threshold for IPSP conductance change
    ES = 5#input("Excitatory synaptic conductance factor (0-6): ")
    IS = 3#input("Inhibitory synaptic conductance factor(): ")

    #**********
    TauSyn = 40;  #IPSP time constant
    #**********

    Stim = 1;  #Endodginous burster


    for T = 2:Last
    for rk = 1:4  #Fourth Order Runge-Kutta
    XH = X[:, T-1] + K[:, rkIndex[rk]]*Wt2[rk]
    Tme = Time[T-1] + Wt2[rk]*DT;  #Time upgrade

    K[1, rk] = DT/Tau*(-(17.81 + 47.58*XH[1] + 33.8*XH[1]^2)*(XH[1] - 0.48) - 26*XH[2]*(XH[1] + 0.95) - 1.93*XH[3]*(1 - 0.5*XH[4])*(XH[1] - 1.4) - 3.25*XH[4]*(XH[1] + 0.95) - Stim*(Tme >= 20)*(Tme <= 70) - IS*XH[10]*(XH[1] + 0.92));  
    K[2, rk] = DT/TauR*(-XH[2] + 1.29*XH[1] + 0.79 + 3.3*(XH[1] + 0.38)^2)
    K[3, rk] = DT/TauC*(-XH[3] + 6.65*(XH[1] + 0.86)*(XH[1] + 0.84))
    K[4, rk] = DT/TauH*(-XH[4] + 3.0*XH[3])
    K[9, rk] = DT/TauSyn*(-XH[9] + (XH[5] > SynThresh))
    K[10, rk] = DT/TauSyn*(-XH[10] + XH[9])

    K[5, rk] = DT/Tau*(-(17.81 + 47.58*XH[5] + 33.8*XH[5]^2)*(XH[5] - 0.48) - 26*XH[6]*(XH[5] + 0.95) - 1.93*XH[7]*(1 - 0.5*XH[8])*(XH[5] - 1.4) - 3.25*XH[8]*(XH[5] + 0.95) - ES*XH[12]*(XH[5]));  
    K[6, rk] = DT/TauR*(-XH[6] + 1.29*XH[5] + 0.79 + 3.3*(XH[5] + 0.38)^2)
    K[7, rk] = DT/TauC*(-XH[7] + 6.65*(XH[5] + 0.86)*(XH[5] + 0.84))
    K[8, rk] = DT/TauH*(-XH[8] + 3.0*XH[7])
    K[11, rk] = DT/TauSyn*(-XH[11] + (XH[1] > SynThresh))
    K[12, rk] = DT/TauSyn*(-XH[12] + XH[11])

    # if rem(Tme, 100) ==0
    #     figure(1), ZA = plot(Time, 100*X[1, :], "r-', Time, 100*X[5, :], 'b-'); #set(ZA, 'LineWidth", 2)
    #     xlabel("Time (ms)'); ylabel('Potential (mV)")
    #     pause(0.1)
    # end

    end
    X[:, T] = X[:, T-1] + sum((Weights.*K)', 1)'/6
    end

    ### PlotlyJS ###
    trace1 = PlotlyJS.scatter(;x=Time, y=100*X[1, :], mode="lines", line_color="red")
    trace2 = PlotlyJS.scatter(;x=Time, y=100*X[5, :], mode="lines", line_color="blue")
    layout = PlotlyJS.Layout(title="Solution", xlabel="Time (ms)", ylabel="Potential (mV)")
    p1 = PlotlyJS.plot([trace1, trace2], layout)
    ### PlotlyJS ###
    # figure(1), ZA = plot(Time, 100*X[1, :], "r-', Time, 100*X[5, :], 'b-'); set(ZA, 'LineWidth", 2)
    # xlabel("Time (ms)'); ylabel('Potential (mV)")


    Spike_Height = maximum(X[1, :])
    Tm = find(X[1, :] .== Spike_Height)[1]
    Half_Ht = (Spike_Height - X[1, 1])/2 + X[1, 1]

    array = X[1, 1:Tm] .>= Half_Ht
    Value = maximum(array)
    Up = find(array .== Value)[1]

    array = X[1, 1:Tm] .<= Half_Ht
    Value = maximum(array)
    Down = find(array .== Value)[1]

    Spike_Width_ms = (Down + Tm - Up)*DT
    #PotentialChange = 100*(min(X[1, Last/2:Last]) - X[1, 1])
    Spikes = (X[1, 1:Last - 1] .< -0.12).*(X[1, 2:Last] .>= -0.12)
    SpkTime = zeros(1, sum(Spikes))
    Nspk = 1;  #Number of spike
    for T = 1:length(Spikes);  #Calculate spike rate for all interspike intervals
    if Spikes[T] == 1; SpkTime[Nspk] = T*DT; Nspk = Nspk + 1; end
    end
    Final = length(SpkTime)
    Rates = 1000./(SpkTime[2:Final] - SpkTime[1:Final - 1])
    Rates'

    p1
end

LGN2cell (generic function with 1 method)

In [54]:
LGN2cell()

# LGNoscillator

In [79]:
function LGNoscillator(XH, Stim, Xinhib, DT, Tau, TauR, TauC, TauH, ES, IS, II, TauSyn, Tme, SynThresh)
    #Function for interacting E & I LGN neurons
    K = zeros(1, 14)
    K[1] = DT/Tau*(-(17.81 + 47.58*XH[1] + 33.8*XH[1]^2)*(XH[1] - 0.48) - 26*XH[2]*(XH[1] + 0.95) - 1.93*XH[3]*(1 - 0.5*XH[4])*(XH[1] - 1.4) - 3.25*XH[4]*(XH[1] + 0.95) - IS*XH[10]*(XH[1] + 0.92));  
    K[2] = DT/TauR*(-XH[2] + 1.29*XH[1] + 0.79 + 3.3*(XH[1] + 0.38)^2)
    K[3] = DT/TauC*(-XH[3] + 6.65*(XH[1] + 0.86)*(XH[1] + 0.84))
    K[4] = DT/TauH*(-XH[4] + 3.0*XH[3])
    K[9] = DT/TauSyn*(-XH[9] + (XH[5] > SynThresh) + (Xinhib > SynThresh))
    K[10] = DT/TauSyn*(-XH[10] + XH[9])

    K[5] = DT/Tau*(-(17.81 + 47.58*XH[5] + 33.8*XH[5]^2)*(XH[5] - 0.48) - 26*XH[6]*(XH[5] + 0.95) - 1.93*XH[7]*(1 - 0.5*XH[8])*(XH[5] - 1.4) - 3.25*XH[8]*(XH[5] + 0.95) - ES*XH[12]*(XH[5]) + Stim*(Tme >= 20)*(Tme <= 70)  - II*XH[14]*(XH[1] + 0.92));  
    K[6] = DT/TauR*(-XH[6] + 1.29*XH[5] + 0.79 + 3.3*(XH[5] + 0.38)^2)
    K[7] = DT/TauC*(-XH[7] + 6.65*(XH[5] + 0.86)*(XH[5] + 0.84))
    K[8] = DT/TauH*(-XH[8] + 3.0*XH[7])
    K[11] = DT/TauSyn*(-XH[11] + (XH[1] > SynThresh))
    K[12] = DT/TauSyn*(-XH[12] + XH[11])
    K[13] = DT/TauSyn*(-XH[13] + (Xinhib > SynThresh))
    K[14] = DT/TauSyn*(-XH[14] + XH[13])
    Response = K'
    return Response
end


LGNoscillator (generic function with 2 methods)

# LGNsynchrony.m

In [86]:
function LGNsynchrony()
    Total_Neurons = 28;  #Solve for this number of interacting Neurons
    DT = 0.1;  #Time increment
    Final_Time = 1100;   #Final time value for calculation
    Last = Int64(Final_Time/DT + 1);  #Last time step
    Time = DT*(0:Last-1);  #Time vector
    Tau = 0.97;  #Neural time constants in msec
    TauR = 5.6
    TauC = 30;  #Tau for Ca++ entry
    TauH = 100;  #Tau for Iahp potential
    WTS = [1 2 2 1];  #Runge-Kutta Coefficient weights

    # Predefine X, K and WTS for speed
    X = Array{Float64}(Total_Neurons, Last)
    K = Array{Float64}(Total_Neurons, 4)
    Weights = Array{Float64}(Total_Neurons, 4)

    for NU = 1:Total_Neurons;  #Initialize
        X[NU, :] = zeros(1, Last);  #Vector to store response of Neuron #1
        K[NU, :] = zeros(1, 4);  #Runge-Kutta terms	
        Weights[NU, :] = WTS;  #Make into matrix for efficiency in main loop
    end

    X[1, 1] = -0.736;  #Initial conditions here if different from zero
    X[2, 1] = 0.258;  #Initial conditions here if different from zero
    X[3, 1] = 0.095;  #Initial conditions here if different from zero
    X[4, 1] = 0.323;  #Initial conditions here if different from zero
    X[5, 1] = -0.736;  #Initial conditions here if different from zero
    X[6, 1] = 0.258;  #Initial conditions here if different from zero
    X[7, 1] = 0.095;  #Initial conditions here if different from zero
    X[8, 1] = 0.323;  #Initial conditions here if different from zero
    X[15, 1] = -0.736;  #Initial conditions here if different from zero
    X[16, 1] = 0.258;  #Initial conditions here if different from zero
    X[17, 1] = 0.095;  #Initial conditions here if different from zero
    X[18, 1] = 0.323;  #Initial conditions here if different from zero
    X[19, 1] = -0.736;  #Initial conditions here if different from zero
    X[20, 1] = 0.258;  #Initial conditions here if different from zero
    X[21, 1] = 0.095;  #Initial conditions here if different from zero
    X[22, 1] = 0.323;  #Initial conditions here if different from zero

    Wt2 = [0 .5 .5 1];  #Second set of RK weights
    rkIndex = [1 1 2 3]
    SynThresh = -0.2;  #Threshold for IPSP conductance change

    ES = 3#input("Excitatory synaptic conductance factor (0-6): ")
    IS = 4#input("Inhibitory synaptic conductance factor(): ")
    II = 2#input("Inhibitory-Inhibitory synaptic conductance factor(): ")

    #**********
    TauSyn = 40;  #IPSP time constant
    #**********

    Stim = 0;  #Endodginous burster

    for T = 2:Last
      for rk = 1:4  #Fourth Order Runge-Kutta
        XH = X[:, T-1] + K[:, rkIndex[rk]]*Wt2[rk]
        Tme =Time[T-1] + Wt2[rk]*DT;  #Time upgrade

        K[1:14, rk] = LGNoscillator(XH[1:14], 0.25, XH[19], DT, Tau, TauR, TauC, TauH, ES, IS, II, TauSyn, Tme, SynThresh)
        K[15:28, rk] = LGNoscillator(XH[15:28], 0, XH[5], DT, Tau, TauR, TauC, TauH, ES, IS, II, TauSyn, Tme, SynThresh)
            
#         if rem(Tme, 100) ==0
#             figure(1), ZA = plot(Time, 100*X[1, :], "r-', Time, 100*X[5, :], 'b-', Time, 100*X[15, :] - 100, 'r-', Time, 100*X[19, :] - 100, 'b-'); #set(ZA, 'LineWidth", 2)
#             xlabel("Time (ms)'); ylabel('Potential (mV)")
#             pause(0.1)
#         end

      end
        X[:, T] = X[:, T-1] + sum((Weights.*K)', 1)'/6
    end

    ### PlotlyJS ###
    trace1 = PlotlyJS.scatter(;x=Time, y=100*X[1, :], mode="lines", line_color="red")
    trace2 = PlotlyJS.scatter(;x=Time, y=100*X[5, :], mode="lines", line_color="blue")
    trace3 = PlotlyJS.scatter(;x=Time, y=100*X[15, :], mode="lines", line_color="red")
    trace4 = PlotlyJS.scatter(;x=Time, y=100*X[19, :], mode="lines", line_color="blue")
    layout = PlotlyJS.Layout(title="Solutions", xlabel="Time (ms)", ylabel="Potential (mV)")
    p1 = PlotlyJS.plot([trace1, trace2, trace3, trace4], layout)
    ### PlotlyJS ###
    # figure(1), ZA = plot(Time, 100*X[1, :], "r-', Time, 100*X[5, :], 'b-', Time, 100*X[15, :] - 100, 'r-', Time, 100*X[19, :] - 100, 'b-'); #set(ZA, 'LineWidth", 2)
    # xlabel("Time (ms)'); ylabel('Potential (mV)")

    Spike_Height = maximum(X[1, :])
    Tm = find(X[1, :] .== Spike_Height)[1]

    Half_Ht = (Spike_Height - X[1, 1])/2 + X[1, 1]

    array = X[1, 1:Tm] .>= Half_Ht
    Value = maximum(array)
    Up = find(array .== Value)[1]

    array = X[1, 1:Tm] .<= Half_Ht
    Value = maximum(array)
    Down = find(array .== Value)[1]


    #PotentialChange = 100*(min(X[1, Last/2:Last]) - X[1, 1])
    Spikes = (X[1, 1:Last - 1] .< -0.12).*(X[1, 2:Last] .>= -0.12)
    SpkTime = zeros(1, sum(Spikes))
    Nspk = 1;  #Number of spike
    for T = 1:length(Spikes);  #Calculate spike rate for all interspike intervals
        if Spikes[T] == 1; SpkTime[Nspk] = T*DT; Nspk = Nspk + 1; end
    end
    Final = length(SpkTime)
    Rates = 1000./(SpkTime[2:Final] - SpkTime[1:Final - 1])
    p1
    
end

LGNsynchrony (generic function with 1 method)

In [87]:
LGNsynchrony()